In [1]:
import pandas as pd

# 读取文件
df = pd.read_csv("638.csv", index_col=0)

# 输出列数和前几列名
print(f"列数（基因数 + 其他列）: {df.shape[1]}")
print("前10列名:", df.columns[:10].tolist())

列数（基因数 + 其他列）: 639
前10列名: ['Dataset', 'IGHA1', 'IGK', 'IGHM', 'IGLJ3', 'CTSH', 'RCN2', 'IGHA2', 'MRPL4', 'ALG8']


In [2]:
import joblib
import pandas as pd
import numpy as np
import os
from sklearn.inspection import permutation_importance
import glob

# -------------------- Step 1: 加载表达数据 --------------------
X_all = pd.read_csv("638.csv", index_col=0)
X = X_all.drop(columns=["Dataset"])  # 删除非基因列
selected_genes = X.columns.tolist()

# -------------------- Step 2: 合并 metadata 生成 y --------------------
metadata_files = glob.glob("../metadata/*.csv")  # 7 个 metadata 文件
label_dfs = []

for file in metadata_files:
    df = pd.read_csv(file)
    if "SampleID" in df.columns and "label" in df.columns:
        label_dfs.append(df[["SampleID", "label"]])
    else:
        print(f"⚠️ 文件 {file} 缺少 SampleID 或 label 列，已跳过")

# 合并为一个完整标签表
label_df = pd.concat(label_dfs, ignore_index=True).drop_duplicates()
label_df = label_df.set_index("SampleID")

# 对齐表达数据
y = label_df.loc[X.index, "label"]

# -------------------- Step 3: 加载模型路径 --------------------
model_paths = {
    "ElasticNet": "elasticnet_model.pkl",
    "RandomForest": "random_forest_model.pkl",
    "XGBoost": "xgboost_model.pkl",
    "SVM_RBF": "svm_rbf_model.pkl",
    "Stacking": "stacking_model.pkl"
}

# -------------------- Step 4: 提取特征重要性并输出 top100 基因 --------------------
os.makedirs("top_genes", exist_ok=True)
gene_scores = {}

for name, path in model_paths.items():
    try:
        print(f"\n▶ 正在处理模型：{name}")
        model = joblib.load(path)

        if hasattr(model, "steps"):
            model = model.steps[-1][1]

        # 特殊处理：SVM
        if name == "SVM_RBF":
            result = permutation_importance(model, X, y, n_repeats=10, random_state=42, scoring='roc_auc')
            importance = result.importances_mean

        # 特殊处理：Stacking
        elif name == "Stacking":
            base_models = model.estimators_
            importances = []
            for base in base_models:
                if hasattr(base, 'feature_importances_'):
                    importances.append(base.feature_importances_)
                elif hasattr(base, 'coef_'):
                    importances.append(base.coef_.flatten())
            if not importances:
                print(f"{name} 中所有基模型均不支持重要性提取，跳过")
                continue
            importance = np.mean(np.array(importances), axis=0)

        # 常规模型
        elif hasattr(model, "coef_"):
            importance = model.coef_.flatten()
        elif hasattr(model, "feature_importances_"):
            importance = model.feature_importances_
        else:
            print(f"{name} 无法提取特征重要性，跳过")
            continue

        # 检查维度匹配
        if len(importance) != len(selected_genes):
            raise ValueError(f"{name} 特征数量 {len(importance)} 与基因数 {len(selected_genes)} 不一致")

        # 构建 DataFrame 并排序
        df = pd.DataFrame({
            "gene": selected_genes,
            f"{name}_score": importance
        }).sort_values(by=f"{name}_score", ascending=False)

        # 保存前 100 个基因
        df["gene"].head(100).to_csv(f"top_genes/{name}_top100_genes.txt", index=False, header=False)
        gene_scores[name] = df

        print(f"✅ {name} 提取成功，前5基因：\n", df.head())

    except Exception as e:
        print(f"❌ {name} 提取失败：{e}")


▶ 正在处理模型：ElasticNet
✅ ElasticNet 提取成功，前5基因：
       gene  ElasticNet_score
192  DUSP5          0.011230
421  ADAT1          0.009831
317  RNF44          0.008788
321  CRTAP          0.008607
124   CTSO          0.008351

▶ 正在处理模型：RandomForest
✅ RandomForest 提取成功，前5基因：
      gene  RandomForest_score
30  CKAP2            0.011135
3   IGLJ3            0.010117
0   IGHA1            0.007845
2    IGHM            0.007620
6   IGHA2            0.005832

▶ 正在处理模型：XGBoost
✅ XGBoost 提取成功，前5基因：
        gene  XGBoost_score
30    CKAP2       0.028692
537   CXCL3       0.019011
118  MRPL15       0.018602
288    MYH9       0.015142
420  MAN2A1       0.014637

▶ 正在处理模型：SVM_RBF
❌ SVM_RBF 提取失败：Input y_true contains NaN.

▶ 正在处理模型：Stacking
✅ Stacking 提取成功，前5基因：
       gene  Stacking_score
432  SRP14        0.020813
3    IGLJ3        0.015095
30   CKAP2        0.015064
552  DHDDS        0.014329
596   CPOX        0.013336


/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:486: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/utils/_array_api.py:390: RuntimeWarning: invalid value encountered in cast
  return x.astype(dtype, copy=copy, casting=casting)


In [3]:
print("SVM_RBF 预测示例：", model.predict(X.iloc[:5]))

SVM_RBF 预测示例： [1 1 1 1 1]


/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:486: UserWarning: X has feature names, but RandomForestClassifier was fitted without feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:486: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(


In [4]:
import joblib
import pandas as pd
import numpy as np
import os
import glob
from sklearn.inspection import permutation_importance

# -------------------- Step 1: 读取表达矩阵 --------------------
X_all = pd.read_csv("638.csv", index_col=0)
X = X_all.drop(columns=["Dataset"])
selected_genes = X.columns.tolist()

# -------------------- Step 2: 合并 metadata 生成 y --------------------
metadata_files = glob.glob("../metadata/*.csv")
if not metadata_files:
    raise FileNotFoundError("❌ 没有找到 metadata 文件，请确认路径是否正确")

label_dfs = []
for file in metadata_files:
    df = pd.read_csv(file)
    if "SampleID" in df.columns and "label" in df.columns:
        label_dfs.append(df[["SampleID", "label"]])
    else:
        print(f"⚠️ 文件 {file} 缺少 SampleID 或 label，已跳过")

if not label_dfs:
    raise ValueError("❌ 所有 metadata 文件都缺失有效标签")

label_df = pd.concat(label_dfs, ignore_index=True).drop_duplicates()
label_df = label_df.set_index("SampleID")

y = label_df.loc[X.index, "label"]  # 保证顺序一致
# 去除没有 label 的样本
valid_mask = ~y.isna()
X = X.loc[valid_mask]
y = y.loc[valid_mask]

# -------------------- Step 3: 加载模型 --------------------
model = joblib.load("svm_rbf_model.pkl")
if hasattr(model, "steps"):
    model = model.steps[-1][1]  # pipeline 取最后一步

# -------------------- Step 4: permutation importance --------------------
print("▶ 正在对 SVM_RBF 计算 permutation importance...")
X_array = X.values  # ❗去掉 feature name，避免 sklearn 报错

result = permutation_importance(
    model, X_array, y,
    n_repeats=10,
    random_state=42,
    scoring='roc_auc'
)

importance = result.importances_mean
print("前10个重要性值:", importance[:10])

# fallback（如果 importance 全为 0）
if np.all(importance == 0) or np.isnan(importance).all():
    print("⚠️ 所有 importance 为 0 或 NaN，自动添加微小扰动")
    importance = np.random.rand(len(selected_genes)) * 1e-6

# -------------------- Step 5: 保存前100基因 --------------------
df = pd.DataFrame({
    "gene": selected_genes,
    "SVM_RBF_score": importance
}).sort_values(by="SVM_RBF_score", ascending=False)

os.makedirs("top_genes", exist_ok=True)
df["gene"].head(100).to_csv("top_genes/SVM_RBF_top100_genes.txt", index=False, header=False)
print("✅ SVM_RBF 提取完成，已保存 top_genes/SVM_RBF_top100_genes.txt")

▶ 正在对 SVM_RBF 计算 permutation importance...
前10个重要性值: [-6.68630275e-04 -1.28996195e-05 -1.22546385e-04 -5.28884398e-04
  1.11022302e-17 -8.38475265e-05 -1.07496829e-05  7.30978436e-05
  3.07440930e-04  2.57992389e-05]
✅ SVM_RBF 提取完成，已保存 top_genes/SVM_RBF_top100_genes.txt


In [5]:
import os
import pandas as pd
from collections import Counter

# 设置目录
top_genes_dir = "top_genes"

# 获取所有 top100 文件
files = [f for f in os.listdir(top_genes_dir) if f.endswith("_top100_genes.txt")]

# 统计出现频率
gene_counter = Counter()

for file in files:
    path = os.path.join(top_genes_dir, file)
    genes = pd.read_csv(path, header=None)[0].tolist()
    gene_counter.update(set(genes))  # 用 set 去重，确保每个文件中每个基因只计一次

# 转换为 DataFrame
freq_df = pd.DataFrame(gene_counter.items(), columns=["gene", "frequency"])
freq_df = freq_df.sort_values(by="frequency", ascending=False)

# 保存为 CSV
freq_df.to_csv("top_genes/gene_frequency_across_models.csv", index=False)

# 展示前10个高频基因
print("✅ 基因出现频率（前10）：\n", freq_df.head(51))

✅ 基因出现频率（前10）：
          gene  frequency
50     ATP2A3          5
53      ISG15          5
62     IFITM1          4
34       IDUA          4
5        ALG8          4
60     SORBS1          4
0       IGLJ3          3
42       SDC3          3
45       RCN2          3
56      EXTL2          3
58        FN1          3
73     MT1HL1          3
28    SIGMAR1          3
75      TIMP2          3
83      SNRPE          3
85     TMEM33          3
95       GRB2          3
98      CKAP2          3
101     ADAT1          3
117     CRTAP          3
30     RNASE6          3
109    BCKDHB          3
11     HNRNPK          3
13      PAICS          3
15     DEFB4B          3
6      ATRAID          3
12   MAPKAPK2          3
4        RORA          3
130  PPP1R14B          2
123    SLC5A6          2
291     CYAT1          2
288   ATP5F1B          2
129     GANAB          2
22       CNBP          2
284      NME1          2
136    RANBP6          2
293    VPREB1          2
137    DNAJA1          2
282     R

In [36]:
import pandas as pd
import mygene

# 读取基因频率文件
df = pd.read_csv("top_genes/gene_frequency_across_models.csv")

# 使用 mygene 查询合法 gene symbol
mg = mygene.MyGeneInfo()
genes = df["gene"].tolist()
results = mg.querymany(genes, scopes="symbol", fields="symbol", species="human", as_dataframe=True)

# 只保留合法 gene（非 notfound）
valid_genes = results[~results["notfound"].fillna(False)].index.tolist()

# 保存为只包含基因名的一列
df_valid = pd.DataFrame({"gene": valid_genes})
df_valid.to_csv("top_genes/gene_valid_for_gsea.txt", index=False, header=False)

print("✅ 合法基因已保存，共", len(df_valid), "个")

Input sequence provided is already in string format. No operation performed
Input sequence provided is already in string format. No operation performed
2 input query terms found dup hits:	[('SNORD36B', 2), ('PMS2P9', 2)]
1 input query terms found no hit:	['ILVBL']


✅ 合法基因已保存，共 298 个


/var/folders/j3/_3qg9gs11jjc7473nnygd52r0000gn/T/ipykernel_2365/2552094096.py:13: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  valid_genes = results[~results["notfound"].fillna(False)].index.tolist()


In [40]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.inspection import permutation_importance
from kneed import KneeLocator
import joblib
import os
from sklearn.pipeline import Pipeline

# ========= 路径设置 ==========
data_path = "AUC0.6.csv"
metadata_dir = "../metadata"
output_dir = "shap_knee"
os.makedirs(output_dir, exist_ok=True)

# ========= 读取表达矩阵 ==========
X = pd.read_csv(data_path, index_col=0)
X = X.loc[:, X.dtypes != "object"]
genes = X.columns.tolist()

# ========= 汇总所有 label ==========
label_dfs = []
for file in os.listdir(metadata_dir):
    if file.endswith(".csv"):
        df = pd.read_csv(os.path.join(metadata_dir, file))
        if "SampleID" in df.columns and "label" in df.columns:
            label_dfs.append(df[["SampleID", "label"]])
label_df = pd.concat(label_dfs, ignore_index=True).drop_duplicates()
label_df = label_df.set_index("SampleID")

# ========= 对齐标签与表达矩阵 ==========
y = label_df.loc[X.index, "label"]

# 修复问题2：处理缺失标签
print(f"标签缺失值检查: {y.isna().sum()}个缺失")
if y.isna().any():
    print("⚠️ 删除缺失标签的样本")
    valid_idx = y.dropna().index
    X = X.loc[valid_idx]
    y = y.loc[valid_idx]

# ========= 模型路径设置 ==========
model_paths = {
    "ElasticNet": "elasticnet_model.pkl",
    "RandomForest": "random_forest_model.pkl",
    "XGBoost": "xgboost_model.pkl",
    "SVM_RBF": "svm_rbf_model.pkl",
    "Stacking": "stacking_model.pkl",
}

# ========= 自动提取重要性 + 绘制肘部图 ==========
knee_results = {}

for name, path in model_paths.items():
    print(f"\n▶ 正在处理模型: {name}")
    
    if name == "Stacking":
        print("⚠️ Stacking 无法直接提取特征重要性，跳过")
        continue
        
    model = joblib.load(path)
    
    # 修复问题1：从Pipeline中提取最终估计器
    if isinstance(model, Pipeline):
        estimator = model.named_steps[list(model.named_steps.keys())[-1]]
        print(f"  从Pipeline中提取估计器: {type(estimator).__name__}")
    else:
        estimator = model

    try:
        # 统一使用排列重要性计算方法
        result = permutation_importance(
            model,  # 使用完整Pipeline
            X.values, 
            y.values, 
            n_repeats=10, 
            random_state=42, 
            scoring="roc_auc",
            n_jobs=-1  # 并行加速
        )
        scores = result.importances_mean
        
        # 确保scores是一维数组
        if scores.ndim > 1:
            print(f"⚠️ 检测到多维重要性分数 ({scores.shape})，取平均值")
            scores = np.mean(scores, axis=0)
        
        # 排序特征重要性
        sorted_idx = np.argsort(scores)[::-1]
        sorted_scores = scores[sorted_idx]
        sorted_genes = np.array(genes)[sorted_idx]

        # 自动识别肘部点
        x = list(range(1, len(sorted_scores)+1))
        kneedle = KneeLocator(
            x, 
            sorted_scores, 
            curve="convex", 
            direction="decreasing",
            interp_method="polynomial",  # 更精确的插值方法
            polynomial_degree=7
        )
        knee_point = kneedle.knee if kneedle.knee else min(50, len(genes)//2)

        # 绘制特征重要性曲线
        plt.figure(figsize=(10, 6))
        plt.plot(x, sorted_scores, 'b-', linewidth=2, label="重要性分数")
        plt.axvline(knee_point, color='r', linestyle='--', 
                   label=f'肘部点 (k={knee_point})')
        plt.scatter(knee_point, sorted_scores[knee_point-1], 
                   s=200, c='red', zorder=5)
        
        plt.xlabel("特征排序", fontsize=12)
        plt.ylabel("重要性分数", fontsize=12)
        plt.title(f"{name} 特征重要性排序", fontsize=14)
        plt.legend(fontsize=10)
        plt.grid(alpha=0.3)
        plt.tight_layout()
        
        plt.savefig(f"{output_dir}/{name}_knee_plot.png", dpi=300)
        plt.savefig(f"{output_dir}/{name}_knee_plot.pdf")
        plt.close()

        # 保存重要基因列表
        pd.DataFrame({
            'Gene': sorted_genes[:knee_point],
            'Importance': sorted_scores[:knee_point]
        }).to_csv(f"{output_dir}/{name}_top_features.csv", index=False)
        
        knee_results[name] = knee_point
        print(f"✅ {name} 肘部点: {knee_point} | 选择 {knee_point} 个特征")

    except Exception as e:
        print(f"❌ {name} 提取失败: {str(e)}")
        import traceback
        traceback.print_exc()

# ========= 保存肘部点表格 ==========
knee_df = pd.DataFrame(list(knee_results.items()), columns=["Model", "KneePoint"])
knee_df.to_csv(f"{output_dir}/knee_summary.csv", index=False)

print("\n" + "="*50)
print(f"🎯 所有模型处理完成！结果保存在: {output_dir}")
print(f"📊 生成模型数量: {len(knee_results)}/{len(model_paths)-1}")
print("="*50)

标签缺失值检查: 36个缺失
⚠️ 删除缺失标签的样本

▶ 正在处理模型: ElasticNet
  从Pipeline中提取估计器: LogisticRegression


/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/joblib/externals/loky/process_executor.py:782: UserWarning: A worker stopped while some jobs were given to the executor. This can be caused by a too short worker timeout or by a memory leak.
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have v

✅ ElasticNet 肘部点: 60 | 选择 60 个特征

▶ 正在处理模型: RandomForest
  从Pipeline中提取估计器: RandomForestClassifier


/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  

✅ RandomForest 肘部点: 43 | 选择 43 个特征

▶ 正在处理模型: XGBoost
  从Pipeline中提取估计器: XGBClassifier


/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  

✅ XGBoost 肘部点: 43 | 选择 43 个特征

▶ 正在处理模型: SVM_RBF
  从Pipeline中提取估计器: SVC


/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  

✅ SVM_RBF 肘部点: 40 | 选择 40 个特征

▶ 正在处理模型: Stacking
⚠️ Stacking 无法直接提取特征重要性，跳过

🎯 所有模型处理完成！结果保存在: shap_knee
📊 生成模型数量: 4/4


/var/folders/j3/_3qg9gs11jjc7473nnygd52r0000gn/T/ipykernel_2365/374967590.py:118: UserWarning: Glyph 29305 (\N{CJK UNIFIED IDEOGRAPH-7279}) missing from font(s) DejaVu Sans.
  plt.tight_layout()
/var/folders/j3/_3qg9gs11jjc7473nnygd52r0000gn/T/ipykernel_2365/374967590.py:118: UserWarning: Glyph 24449 (\N{CJK UNIFIED IDEOGRAPH-5F81}) missing from font(s) DejaVu Sans.
  plt.tight_layout()
/var/folders/j3/_3qg9gs11jjc7473nnygd52r0000gn/T/ipykernel_2365/374967590.py:118: UserWarning: Glyph 25490 (\N{CJK UNIFIED IDEOGRAPH-6392}) missing from font(s) DejaVu Sans.
  plt.tight_layout()
/var/folders/j3/_3qg9gs11jjc7473nnygd52r0000gn/T/ipykernel_2365/374967590.py:118: UserWarning: Glyph 24207 (\N{CJK UNIFIED IDEOGRAPH-5E8F}) missing from font(s) DejaVu Sans.
  plt.tight_layout()
/var/folders/j3/_3qg9gs11jjc7473nnygd52r0000gn/T/ipykernel_2365/374967590.py:118: UserWarning: Glyph 37325 (\N{CJK UNIFIED IDEOGRAPH-91CD}) missing from font(s) DejaVu Sans.
  plt.tight_layout()
/var/folders/j3/_3qg9gs11

In [6]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.inspection import permutation_importance
from kneed import KneeLocator
import joblib
import os
from sklearn.pipeline import Pipeline

# ========= Paths ==========
data_path = "638.csv"
metadata_dir = "../metadata"
output_dir = "shap_knee"
os.makedirs(output_dir, exist_ok=True)

# ========= Load expression matrix ==========
X = pd.read_csv(data_path, index_col=0)
X = X.loc[:, X.dtypes != "object"]
genes = X.columns.tolist()

# ========= Load and align labels ==========
label_dfs = []
for file in os.listdir(metadata_dir):
    if file.endswith(".csv"):
        df = pd.read_csv(os.path.join(metadata_dir, file))
        if "SampleID" in df.columns and "label" in df.columns:
            label_dfs.append(df[["SampleID", "label"]])
label_df = pd.concat(label_dfs, ignore_index=True).drop_duplicates()
label_df = label_df.set_index("SampleID")

y = label_df.loc[X.index, "label"]

# Handle missing labels
print(f"Missing labels: {y.isna().sum()}")
if y.isna().any():
    print("⚠️ Removing samples with missing labels")
    valid_idx = y.dropna().index
    X = X.loc[valid_idx]
    y = y.loc[valid_idx]

# ========= Model paths ==========
model_paths = {
    "ElasticNet": "elasticnet_model.pkl",
    "RandomForest": "random_forest_model.pkl",
    "XGBoost": "xgboost_model.pkl",
    "SVM_RBF": "svm_rbf_model.pkl",
    "Stacking": "stacking_model.pkl",
}

# ========= Extract importance and plot knee ==========
knee_results = {}

for name, path in model_paths.items():
    print(f"\n▶ Processing model: {name}")
    
    if name == "Stacking":
        print("⚠️ Skipping Stacking (no direct importance)")
        continue

    model = joblib.load(path)

    # Extract estimator from pipeline
    if isinstance(model, Pipeline):
        estimator = model.named_steps[list(model.named_steps.keys())[-1]]
        print(f"  Extracted estimator: {type(estimator).__name__}")
    else:
        estimator = model

    try:
        result = permutation_importance(
            model, X.values, y.values,
            n_repeats=10,
            random_state=42,
            scoring="roc_auc",
            n_jobs=-1
        )
        scores = result.importances_mean

        if scores.ndim > 1:
            print(f"⚠️ Detected multi-dimensional importance scores: {scores.shape}")
            scores = np.mean(scores, axis=0)

        sorted_idx = np.argsort(scores)[::-1]
        sorted_scores = scores[sorted_idx]
        sorted_genes = np.array(genes)[sorted_idx]

        x = list(range(1, len(sorted_scores)+1))
        kneedle = KneeLocator(
            x, sorted_scores, curve="convex", direction="decreasing",
            interp_method="polynomial", polynomial_degree=7
        )
        knee_point = kneedle.knee if kneedle.knee else min(50, len(genes)//2)

        # === Plot ===
        plt.figure(figsize=(10, 6))
        plt.plot(x, sorted_scores, 'b-', linewidth=2, label="Importance Score")
        plt.axvline(knee_point, color='r', linestyle='--', label=f'Knee Point (k={knee_point})')
        plt.scatter(knee_point, sorted_scores[knee_point - 1], s=200, c='red', zorder=5)

        plt.xlabel("Feature Rank", fontsize=12)
        plt.ylabel("Importance Score", fontsize=12)
        plt.title(f"{name} Feature Importance", fontsize=14)
        plt.legend(fontsize=10)
        plt.grid(alpha=0.3)
        plt.tight_layout()

        # Only save PNG
        plt.savefig(f"{output_dir}/{name}_knee_plot.png", dpi=300)
        plt.close()

        # Save top features
        pd.DataFrame({
            'Gene': sorted_genes[:knee_point],
            'Importance': sorted_scores[:knee_point]
        }).to_csv(f"{output_dir}/{name}_top_features.csv", index=False)

        knee_results[name] = knee_point
        print(f"✅ {name} knee point: {knee_point} features selected")

    except Exception as e:
        print(f"❌ Failed on {name}: {str(e)}")
        import traceback
        traceback.print_exc()

# ========= Save knee summary ==========
knee_df = pd.DataFrame(list(knee_results.items()), columns=["Model", "KneePoint"])
knee_df.to_csv(f"{output_dir}/knee_summary.csv", index=False)

print("\n" + "="*50)
print(f"🎯 All models completed. Results saved in: {output_dir}")
print(f"📊 Models processed: {len(knee_results)}/{len(model_paths)-1}")
print("="*50)

Missing labels: 36
⚠️ Removing samples with missing labels

▶ Processing model: ElasticNet
  Extracted estimator: LogisticRegression


/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  

✅ ElasticNet knee point: 73 features selected

▶ Processing model: RandomForest
  Extracted estimator: RandomForestClassifier


/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  

✅ RandomForest knee point: 59 features selected

▶ Processing model: XGBoost
  Extracted estimator: XGBClassifier


/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  

✅ XGBoost knee point: 71 features selected

▶ Processing model: SVM_RBF
  Extracted estimator: SVC


/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/kylin/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  

✅ SVM_RBF knee point: 78 features selected

▶ Processing model: Stacking
⚠️ Skipping Stacking (no direct importance)

🎯 All models completed. Results saved in: shap_knee
📊 Models processed: 4/4


In [ ]:
import pandas as pd
import numpy as np
import joblib
import os

# ========= 路径设置 ==========
data_path = "638.csv"
metadata_dir = "../metadata"
output_dir = "stacking_analysis"
os.makedirs(output_dir, exist_ok=True)

# ========= 读取数据 ==========
print("读取数据...")
X = pd.read_csv(data_path, index_col=0)
X = X.loc[:, X.dtypes != "object"]
genes = X.columns.tolist()

# 汇总标签
label_dfs = []
for file in os.listdir(metadata_dir):
    if file.endswith(".csv"):
        df = pd.read_csv(os.path.join(metadata_dir, file))
        if "SampleID" in df.columns and "label" in df.columns:
            label_dfs.append(df[["SampleID", "label"]])
label_df = pd.concat(label_dfs, ignore_index=True).drop_duplicates()
label_df = label_df.set_index("SampleID")

# 对齐数据
y = label_df.loc[X.index, "label"]

# 处理缺失标签
if y.isna().any():
    valid_idx = y.dropna().index
    X = X.loc[valid_idx]
    y = y.loc[valid_idx]

# ========= 加载Stacking模型 ==========
print("\n加载Stacking模型...")
model = joblib.load("stacking_model.pkl")

# ========= 尝试提取模型自带的特征重要性 ==========
def extract_model_importance(model):
    """尝试从模型或最终估计器中提取特征重要性"""
    try:
        # 如果模型本身有特征重要性
        if hasattr(model, 'feature_importances_'):
            return model.feature_importances_
        # 如果模型有系数（如线性模型）
        elif hasattr(model, 'coef_'):
            return np.abs(model.coef_.flatten())
        # 如果模型是Pipeline，检查最终估计器
        elif hasattr(model, 'named_steps'):
            final_estimator = model.named_steps[list(model.named_steps.keys())[-1]]
            if hasattr(final_estimator, 'feature_importances_'):
                return final_estimator.feature_importances_
            elif hasattr(final_estimator, 'coef_'):
                return np.abs(final_estimator.coef_.flatten())
    except:
        pass
    return None

# ========= 替代方法：基于方差的特征选择 ==========
def variance_based_selection(X, genes):
    """基于特征方差选择重要特征"""
    # 计算每个特征的方差
    variances = X.var()
    # 标准化方差
    normalized_var = (variances - variances.min()) / (variances.max() - variances.min())
    # 选择方差大于平均值的特征
    mean_var = normalized_var.mean()
    selected_idx = normalized_var > mean_var
    selected_genes = np.array(genes)[selected_idx]
    return selected_genes, variances

# ========= 主要分析流程 ==========
print("\n分析特征重要性...")

# 1. 尝试使用模型自带的特征重要性
scores = extract_model_importance(model)

if scores is None or np.all(scores == 0):
    print("⚠️ 无法获取有效的特征重要性分数，使用基于方差的方法")
    
    # 使用基于方差的特征选择
    selected_genes, variances = variance_based_selection(X, genes)
    knee_point = len(selected_genes)
    
    # 输出结果
    print("\n" + "="*50)
    print("Stacking模型特征分析结果（基于方差）")
    print("="*50)
    print(f"📊 选择的特征数量: {knee_point}")
    print(f"  占总特征数的比例: {knee_point/len(genes):.1%}")
    print("\n📈 方差统计:")
    print(f"  最小方差: {variances.min():.6f}")
    print(f"  最大方差: {variances.max():.6f}")
    print(f"  平均方差: {variances.mean():.6f}")
    print(f"  阈值方差: {variances.mean():.6f} (平均值)")
    
    # 保存重要特征列表
    sorted_idx = np.argsort(variances)[::-1]
    sorted_genes = np.array(genes)[sorted_idx]
    sorted_variances = variances[sorted_idx]
    
    top_features = pd.DataFrame({
        'Gene': sorted_genes[:knee_point],
        'Variance': sorted_variances[:knee_point]
    })
    top_features_path = f"{output_dir}/Stacking_top_features.csv"
    top_features.to_csv(top_features_path, index=False)
    print(f"\n💾 重要特征列表已保存至: {top_features_path}")

else:
    print("✅ 成功从模型中提取特征重要性")
    
    # 计算基本统计量
    mean_score = np.mean(scores)
    std_score = np.std(scores)
    min_score = np.min(scores)
    max_score = np.max(scores)
    
    # 排序重要性分数
    sorted_idx = np.argsort(scores)[::-1]
    sorted_genes = np.array(genes)[sorted_idx]
    sorted_scores = scores[sorted_idx]
    
    # 计算累积重要性
    cumulative = np.cumsum(sorted_scores)
    total_importance = cumulative[-1]
    cumulative_proportion = cumulative / total_importance
    
    # 找到累积比例达到95%的点
    knee_point = np.argmax(cumulative_proportion >= 0.95) + 1
    
    # 输出结果
    print("\n" + "="*50)
    print("Stacking模型特征分析结果")
    print("="*50)
    print(f"📊 计算得到的肘部点: {knee_point}")
    print(f"  即选择前{knee_point}个最重要特征")
    print("\n📈 重要性分数统计分布:")
    print(f"  平均值: {mean_score:.6f}")
    print(f"  标准差: {std_score:.6f}")
    print(f"  最小值: {min_score:.6f}")
    print(f"  最大值: {max_score:.6f}")
    print(f"  总重要性: {total_importance:.6f}")
    print(f"  肘部点累积重要性: {cumulative_proportion[knee_point-1]:.2%}")
    
    # 保存重要特征列表
    top_features = pd.DataFrame({
        'Gene': sorted_genes[:knee_point],
        'Importance': sorted_scores[:knee_point]
    })
    top_features_path = f"{output_dir}/Stacking_top_features.csv"
    top_features.to_csv(top_features_path, index=False)
    print(f"\n💾 重要特征列表已保存至: {top_features_path}")

print("\n✅ 分析完成")

读取数据...

加载Stacking模型...

分析特征重要性...
⚠️ 无法获取有效的特征重要性分数，使用基于方差的方法

Stacking模型特征分析结果（基于方差）
📊 选择的特征数量: 193
  占总特征数的比例: 30.3%

📈 方差统计:
  最小方差: 0.139115
  最大方差: 1.228965
  平均方差: 0.336739
  阈值方差: 0.336739 (平均值)

💾 重要特征列表已保存至: stacking_analysis/Stacking_top_features.csv

✅ 分析完成


/var/folders/j3/_3qg9gs11jjc7473nnygd52r0000gn/T/ipykernel_26051/1748853186.py:103: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  sorted_variances = variances[sorted_idx]


In [10]:
import pandas as pd
import os

# 模型方法名称
methods = ["ElasticNet", "RandomForest", "XGBoost", "SVM_RBF", "Stacking"]

# 存储每种模型的基因集合
gene_dict = {}

# 读取每种模型的 top_features.csv 中的 Gene 列
for method in methods:
    file_path = f"shap_knee/{method}_top_features.csv"
    if os.path.exists(file_path):
        df = pd.read_csv(file_path)
        genes = df["Gene"].dropna().astype(str).unique().tolist()
        gene_dict[method] = genes
        print(f"✅ {method}: {len(genes)} genes")
    else:
        print(f"⚠️ 文件未找到: {file_path}")

# 统一长度，填充空字符串
max_len = max(len(g) for g in gene_dict.values())
gene_table = {k: v + [""] * (max_len - len(v)) for k, v in gene_dict.items()}

# 保存为 CSV 文件（用逗号分隔）
df_out = pd.DataFrame(gene_table)
output_path = "top_genes_for_venn/all_models_gene_sets.csv"
os.makedirs("top_genes_for_venn", exist_ok=True)
df_out.to_csv(output_path, index=False)

print(f"\n✅ CSV 文件已保存至: {output_path}")

✅ ElasticNet: 73 genes
✅ RandomForest: 59 genes
✅ XGBoost: 71 genes
✅ SVM_RBF: 78 genes
✅ Stacking: 193 genes

✅ CSV 文件已保存至: top_genes_for_venn/all_models_gene_sets.csv


In [11]:
import pandas as pd

# 读取合成的CSV文件
df = pd.read_csv("top_genes_for_venn/all_models_gene_sets.csv")

# 将所有列合并为一个 Series，并去除空值
all_genes = pd.concat([df[col] for col in df.columns]).dropna()
all_genes = all_genes[all_genes != ""]  # 移除空字符串

# 统计出现频率
gene_counts = all_genes.value_counts().reset_index()
gene_counts.columns = ["gene", "frequency"]

# 保存结果
output_path = "top_genes_for_venn/gene_frequency.csv"
gene_counts.to_csv(output_path, index=False)

print(f"✅ 统计完成，已保存至：{output_path}")

✅ 统计完成，已保存至：top_genes_for_venn/gene_frequency.csv


In [12]:
import pandas as pd

# 读取原始文件
df = pd.read_csv("top_genes_for_venn/gene_frequency.csv")

# 保留 gene 列
df_gene_only = df[["gene"]]

# 保存为新文件
df_gene_only.to_csv("top_genes_for_venn/gene_list_only.csv", index=False)